# Import

In [3]:
import sys
%load_ext autoreload
%autoreload 2
sys.path.append('../')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [9]:
!pip install ydata-profiling

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 344.5/344.5 kB 831.0 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.5/78.5 kB 553.5 kB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 397.1 kB/s eta 0:00:0000:0100:01
  Using cached htmlmin-0.1.12.tar.gz (19 kB)
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 197.6/197.6 kB 744.6 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 593.1 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 652.9/652.9 kB 672.2 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.7/102.7 kB 1.1 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 1.4 MB/s eta 0:00:0000:0100:010m
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 3.0 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 1.2 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━

In [39]:
import numpy as np
import pandas as pd
from ydata_profiling import ProfileReport
import ipywidgets
from pathlib import Path

from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score

from catboost import CatBoostClassifier

from src import common

# data

In [11]:
train_values, train_labels = common.file.read_data('train')

In [19]:
df_profile=train_values.join(train_labels)
train_profile=ProfileReport(df_profile, title="Richter's Train Dataset Pandas profile")

train_profile

Render HTML: 100%|███████████████████████████████████████████████████████████████████| 1/1 [00:02<00:00,  2.58s/it]


# preprocessing

In [20]:
features_list = ['geo_level_1_id', 
                 'geo_level_2_id', 
                 'geo_level_3_id',
                 'age', 
                 'area_percentage', 
                 'height_percentage', 
                 'foundation_type', 
                 'roof_type', 
                 'ground_floor_type', 
                 'other_floor_type', 
                 'position', 
                 'has_superstructure_mud_mortar_stone', 
                 'has_superstructure_cement_mortar_brick', 
                 'has_superstructure_timber', 
                 'count_families', 
                 'has_secondary_use'
                ]

In [21]:
train_values, train_labels = common.lgbm_preprocessing((train_values, train_labels), mode='training', features_list=features_list)

In [34]:
cat_features = list(train_values.select_dtypes(include='category').columns)

In [25]:
X_train, X_test, y_train, y_test = train_test_split(train_values, train_labels,
                                                        test_size=0.1, random_state=19, stratify=train_labels)

In [37]:
#input best params here from randm.best_params_
model = CatBoostClassifier(eval_metric='TotalF1',random_seed=19, silent=False, 
                           cat_features=cat_features, iterations=2000, learning_rate=0.1)
model.fit(X_train, y_train)
preds=model.predict(X_test)

0:	learn: 0.6050500	total: 478ms	remaining: 15m 54s
1:	learn: 0.6050500	total: 988ms	remaining: 16m 27s
2:	learn: 0.5908330	total: 1.48s	remaining: 16m 27s
3:	learn: 0.6033373	total: 1.98s	remaining: 16m 30s
4:	learn: 0.6018138	total: 2.46s	remaining: 16m 23s
5:	learn: 0.6024791	total: 3.1s	remaining: 17m 10s
6:	learn: 0.6029273	total: 3.55s	remaining: 16m 50s
7:	learn: 0.6050726	total: 4.03s	remaining: 16m 44s
8:	learn: 0.6002527	total: 4.61s	remaining: 16m 59s
9:	learn: 0.5972690	total: 5.14s	remaining: 17m 2s
10:	learn: 0.6002323	total: 5.67s	remaining: 17m 6s
11:	learn: 0.6026893	total: 6.21s	remaining: 17m 9s
12:	learn: 0.6058170	total: 6.81s	remaining: 17m 21s
13:	learn: 0.6074445	total: 7.42s	remaining: 17m 31s
14:	learn: 0.6038720	total: 8.06s	remaining: 17m 46s
15:	learn: 0.6049728	total: 8.8s	remaining: 18m 10s
16:	learn: 0.6046218	total: 9.55s	remaining: 18m 33s
17:	learn: 0.6068530	total: 10.3s	remaining: 18m 52s
18:	learn: 0.6073684	total: 11s	remaining: 19m 6s
19:	learn: 

In [40]:
preds=model.predict(X_test)

#f1 score is the metric used in the competition
accuracy=f1_score(y_test,preds,average='micro')
print("Score on test set")
print("\n ========================================================")
print(accuracy)
print('\n Benchmark model was: 0.5815')


Score on test set

0.7324738114423852

 Benchmark model was: 0.5815
